# Using dynamic data masking with SUPER data type paths (preview)

In this lab notebook we will explore the mechanism to use dynamic data masking (DDM) in Amazon Redshift, you can protect sensitive data in your data warehouse. You can manipulate how Amazon Redshift shows sensitive data to the user at query time, without transforming it in the database. You control access to data through masking policies that apply custom obfuscation rules to a given user or role.

https://docs.aws.amazon.com/redshift/latest/dg/t_ddm-super.html

# Pre-requisites

1. Create Redshift Serverelss workgroup in preview mode.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html) to create preview wokrgroup.
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

##   Create and load sample data

In [0]:
DROP TABLE IF EXISTS employee;
CREATE TABLE IF NOT EXISTS employee (
    col_person SUPER
);

INSERT INTO employee
VALUES
    (
        json_parse('
            {
                "first_name": "John",
                "last_name": "Doe",
                "age": 25,
                "ssn": "111-22-3333",
                "hire_date":"01/23/2019",
                "phone" : "712-110-8888",
                "email" : "johndoe@gmail.com",
                "base_salary" :"100,000",
                "overtime" :"yes"
            }
        ')
    ),
    (
        json_parse('
            {

                "first_name": "Jane",
                "last_name": "Appleseed",
                "age": 34,
                "ssn": "444-55-7777",
                "hire_date":"08/12/2021",
                "phone" : "832-446-8909",
                "email" : "janeapplessed@gmail.com",
                "base_salary" :"130,000",
                "overtime" :"no"
            }
        ')
    ),
    (
        json_parse('
            {
                "first_name": "vishnu",
                "last_name": "kumar",
                "age": 35,
                "ssn": "897-22-3455",
                "hire_date":"04/05/2021",
                "phone" : "210-360-8734",
                "email" : "vkumar@gmail.com",
                "base_salary" :"110,000",
                "overtime" :"yes"
            }
        ')
    )
;
GRANT ALL ON ALL TABLES IN SCHEMA "public" TO PUBLIC;

## Use Case

ABC organiation would like to implement the following policy guidelines for thier department when it comes to access the employee information

 1. HR Executie -- > as per policy HR Executie should be able to see all employees data, e.g. No Masking plicy applies to them

 2. HR staff -- > as per policy ,they should not be able to see full SSN , Base salary and Overtime information - The policy requires to show last 4 digit of SSN and   for base salary should be displayed as '0' and overtime information shoud be redacted with "XX"
 
 3. Accounts  --> for accounts team requirment is to mask the Phone number with "111-11-1111" and hire_date with a mask value " ** - ** - ****"

## Create Database roles and Users in Amazon Redshift

In [0]:
-- create role for each department 

CREATE ROLE hr_executive;
CREATE ROLE hr_staff;
CREATE ROLE accounts;

-- create users and assign them to respective role 

CREATE USER kim WITH PASSWORD '1234Test!';
CREATE USER vishal  WITH PASSWORD '1234Test!';
CREATE USER jeff  WITH PASSWORD '1234Test!';

-- Grant Roles to Users
GRANT ROLE hr_executive to jeff;
GRANT ROLE hr_staff to vishal;
GRANT ROLE accounts to kim;

# Define Masking Policy

In [0]:
-- This policy converts the first five digits of the given SSN to 'XXX-XX'.
CREATE MASKING POLICY mask_ssn
WITH(ssn TEXT)
USING ( 'XXX-XX-'::TEXT || SUBSTRING(ssn::TEXT FROM 8 FOR 4) );

-- This policy replaces the given name with the fixed string '********'.
CREATE MASKING POLICY mask_base_salary
WITH(base_salary TEXT)
USING ( '0'::TEXT );

CREATE MASKING POLICY mask_overtime
WITH(overtime TEXT)
USING ( 'XX'::TEXT );

CREATE MASKING POLICY mask_hire_date
WITH(hire_date TEXT)
USING ( '** - ** - ****'::TEXT );

CREATE MASKING POLICY mask_phone
WITH(phone TEXT)
USING ( '111-11-1111'::TEXT );

## Apply policy to employee Table based on the usecase

https://docs.aws.amazon.com/redshift/latest/dg/r_ATTACH_MASKING_POLICY.html

In [0]:
ATTACH MASKING POLICY mask_ssn
ON employee(col_person.ssn)
TO ROLE hr_staff;

ATTACH MASKING POLICY mask_base_salary
ON employee(col_person.base_salary)
TO ROLE hr_staff;

ATTACH MASKING POLICY mask_overtime
ON employee(col_person.overtime)
TO ROLE hr_staff;


ATTACH MASKING POLICY mask_phone
ON employee(col_person.phone)
TO ROLE accounts;

ATTACH MASKING POLICY mask_hire_date
ON employee(col_person.hire_date)
TO ROLE accounts;

## Display the policies attached to the table

Use SVV_ATTACHED_MASKING_POLICY to view all the relations and roles/users with policies attached on the currently connected database.

Note : Only superusers and users with the sys:secadmin role can view this information.

https://docs.aws.amazon.com/redshift/latest/dg/r_SVV_ATTACHED_MASKING_POLICY.html

In [0]:
SELECT * FROM svv_attached_masking_policy;

## Test Access for HR Staff Members 

Since Vishal is member of hr_staff , he should  see last 4 digit of SSN and for base salary and overtime information shoud be redacted with "********"

In [0]:
set session AUTHORIZATION 'vishal';

SELECT CURRENT_USER;

SELECT col_person.first_name,col_person.last_name , 
col_person.ssn , 
col_person.hire_date , 
col_person.base_salary,
col_person.overtime
 from employee;

## Test Access for Accounts Members 

Since kim is member of accounts team , for accounts team requirment is to mask the Phone number  and hire_date with a generic mask e.g. "*******"

In [0]:
set session AUTHORIZATION 'kim';

SELECT CURRENT_USER;

SELECT col_person.first_name,col_person.last_name , 
col_person.ssn , 
col_person.hire_date , 
col_person.phone , 
col_person.base_salary,
col_person.overtime
 from employee;

## Test Access for HR Executives 

Since Jeff is member of HR Executives  , no masking policy apply to this group and hence they can see all attributes information

In [0]:
set session AUTHORIZATION 'jeff';

SELECT CURRENT_USER;

SELECT col_person.first_name,col_person.last_name , 
col_person.ssn , 
col_person.hire_date , 
col_person.phone , 
col_person.base_salary,
col_person.overtime
 from employee;

## cleanup

This conclude the lab , please execute below script to detach policy from table and then drop the masking policies

### Note : Please note that below script should be executed by a super user

https://docs.aws.amazon.com/redshift/latest/dg/r_DETACH_MASKING_POLICY.html

In [0]:
-- change the user name to your admin or super user- default for serverless workgroup is 'admin' and provisioned cluster is 'awsuser'
set session AUTHORIZATION 'admin';

DETACH MASKING POLICY mask_ssn
ON employee(col_person.ssn)
FROM ROLE hr_staff;

DETACH MASKING POLICY mask_base_salary
ON employee(col_person.base_salary)
FROM ROLE hr_staff;

DETACH MASKING POLICY mask_overtime
ON employee(col_person.overtime)
FROM ROLE hr_staff;


DETACH MASKING POLICY mask_phone
ON employee(col_person.phone)
FROM ROLE accounts;

DETACH MASKING POLICY mask_hire_date
ON employee(col_person.hire_date)
FROM ROLE accounts;


DROP MASKING POLICY mask_ssn;
DROP MASKING POLICY mask_base_salary;
DROP MASKING POLICY mask_phone;
DROP MASKING POLICY mask_overtime cascade;
DROP MASKING POLICY mask_hire_date;